In [1]:
from h3 import h3
from copy import copy, deepcopy
import folium
import json
from tqdm import tqdm
from random import uniform, randrange
from ipyleaflet import Map, DrawControl, basemaps, basemap_to_tiles, Polygon
import ipywidgets as widgets
import time
import itertools

import pandas as pd

# Exploring H3
The H3 geospatial indexing system is a descrete global grid system (DGGS) consisting of a multi-precision hexagonal tiling of the sphere with hierarchical indexes.  The hexagonal grid system is created on the planar faces of a sphere-circumscribed icosahedron, and the grid cells are then projected to the surface of the sphere using an inverse face-centered polyhedral gnomonic projection.  H3 is similar to other spatial indexes (notably S2 and geohash), the key difference being H3 uses a hexagonal tessalation.

![title](img/DGGS-H3.png)

## H3 Cell
A H3 Cell is defined as a hexagonal grid cell at a given resolution.  Resolution determines the [precision and area](https://uber.github.io/h3/#/documentation/core-library/resolution-table) of the grid cell.  The lowest resolution available is 0, containing 122 unique grid cells (also called base cells), while the highest resolution, 15, contains 569,707,381,193,162 unique cells.


Each hexagonal grid cell of the DGGS is registered with a `h3_address` and a `h3_index`.  The [index](https://uber.github.io/h3/#/documentation/core-library/h3-index-representations) is a unique hierarchical index packed into the lowest order 63 bits of a 64-bit integer.  The address is string serialized representation of the index (similar to a geohash).

In [2]:
# Create an address
h3_address = h3.geo_to_h3(37.3615593, -122.0553238, 15)
h3_index = h3.string_to_h3(h3_address)
print("Address: {}".format(h3_address))
print("Index: {}".format(h3_index))
print("Bytes: {}".format(bin(h3_index)))

Address: 8f283470d921c65
Index: 644722037860998245
Bytes: 0b100011110010100000110100011100001101100100100001110001100101


### Index Structure
The index contains the following elements in order:
- 4 bits to indicate the index mode
- 3 bits reserved
- 4 bits to indicate the cell resolution (0-15)
- 7 bits to indicate the base cell (0-121)
- 3 bits to indicate each subsequent cell number (0-6) from resolution 1 up to the resolution of the cell

In [3]:
class H3Index(object):
    
    def __init__(self, h3_address):
        self.address = h3_address
        self.index = h3.string_to_h3(h3_address)
        self.bits = bin(self.index)[2:]
        self.mode = self.bits[0:4]
        self.resolution = self.bits[4:8]
        self.base_cell = self.bits[8:15]
        self.parents = [self.bits[15:][i:i+3] for i in range(0, len(self.bits[15:]), 3)]
        self.cell = self.parents[int(self.resolution, 2) - 1]

In [4]:
index = H3Index(h3_address)
print("Resolution: {}".format(int(index.resolution, 2)))
print("Base Cell: {}".format(int(index.base_cell, 2)))

Resolution: 15
Base Cell: 20


H3 has very efficient access to parent cells as the cell number of each parent resolution is encoded directly into the index.  At resolution 15, we expect to return a parent cell from all resolutions.

In [5]:
print("Parent Cell Numbers: {}".format([int(x,2) for x in index.parents]))

Parent Cell Numbers: [0, 6, 4, 3, 4, 1, 5, 4, 4, 4, 1, 6, 1, 4, 5]


At resolution 7 we only return 7 valid values as expected

In [6]:
index7 = H3Index(h3.geo_to_h3(37.3615593, -122.0553238, 7))
print("Parent Cell Numbers: {}".format([int(x,2) for x in index7.parents]))

Parent Cell Numbers: [0, 6, 4, 3, 4, 5, 3, 7, 7, 7, 7, 7, 7, 7, 7]


This index structure makes it very easy to rebuild the parent index at any resolution.  The builtin `h3.h3_to_parent` truncates the index to efficiently determine ancestory.

In [7]:
def get_parent(index, res):
    # Update with new resolution
    new_res = format(res, '#06b')[2:]
    new_parents = copy(index.parents)
    # Update parents
    for i in range(res, int(index.resolution, 2)):
        new_parents[i] = '111'
    bits = f"{index.mode}{new_res}{index.base_cell}{''.join(new_parents)}"
    return H3Index(h3.h3_to_string(int(bits, 2)))

parent8 = get_parent(index, 8)

print("Parent cell address: {}".format(parent8.address))

parent8_h3 = h3.h3_to_parent(index.address, 8)

assert parent8.address == parent8_h3

Parent cell address: 88283470d9fffff


We can visualize a cell's ancestry with Folium.  We can see the hierarchical nature of the spatial index as we zoom in.  Note not all cells will appear completely self contained due to distortion when reprojecting from H3 > 4326 > 3857.

In [8]:
def visualize_hexagons(hexagons, color="red", folium_map=None, centroids=False, tiles=None):
    """
    hexagons is a list of hexcluster. Each hexcluster is a list of hexagons. 
    eg. [[hex1, hex2], [hex3, hex4]]
    
    Adapted from https://github.com/uber/h3-py/blob/master/docs/Usage.ipynb
    """
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        if tiles:
            m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles=tiles)
        else:
            m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    else:
        m = folium_map
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=3,color=color)
        m.add_child(my_PolyLine)
    if centroids:
        geo = [h3.h3_to_geo(x) for x in hexagons]
        for item in geo:
            my_marker = folium.Marker(item)
            m.add_child(my_marker)
    return m

In [9]:
hexagons = []
for i in range(h3.h3_get_resolution(h3_address)):
    parent = h3.h3_to_parent(h3_address, i)
    hexagons.append(parent)

lat, lng = h3.h3_to_geo(hexagons[0])

m = folium.Map(location=[lat, lng], zoom_start=4, tiles='cartodbpositron')
m = visualize_hexagons(hexagons, folium_map=m)
display(m)

## Indexing Spaces
A single resolution 15 grid cell is H3's best representation of a point.  H3 represents polygons using many smaller hexagons, called a coverage.  S2 does the same thing as well.  Lets use world city data as a dataset.

#### Data Prep

In [10]:
hexcount = 0
city_dict = {}
with open('cities.geojson', 'r') as geoj:
    cities = json.load(geoj)['features']
    for item in cities:
        cityname = item['properties']['NAME']
        geometry = item['geometry']
        city_dict.update({cityname:geometry})

Generate a coverage of a couple cities using varying zoom levels

In [11]:
def cover_city(name, res):
    city_geom = deepcopy(city_dict[name])
    hexagons = h3.polyfill(city_geom, res, geo_json_conformant=True)
    m = folium.Map(location=city_geom['coordinates'][0][0][::-1], tiles='stamenterrain')
    poly = folium.GeoJson(city_geom, name='geojson').add_to(m)
    m = visualize_hexagons(hexagons, folium_map=m)
    return m

### Seattle

In [12]:
m = cover_city('SEATTLE', 10)
display(m)

### Washington D.C.

In [13]:
m = cover_city('WASHINGTON D. C.', 7)
display(m)

### Cape Town

In [14]:
m = cover_city('CAPE TOWN', 9)
display(m)

## Compact Coverages
H3 allows the "compaction" of coverages which reduces the number of hexagon cells in the coverage while maintaining the shape of the polygon.

In [15]:
def cover_city_compact(name, res):
    city_geom = deepcopy(city_dict[name])
    hexagons = h3.polyfill(city_geom, res, geo_json_conformant=True)
    compacted = h3.compact(hexagons)
    m = folium.Map(location=city_geom['coordinates'][0][0][::-1], tiles='stamenterrain')
    poly = folium.GeoJson(city_geom, name='geojson').add_to(m)
    m = visualize_hexagons(compacted, folium_map=m)
    return m

### Seattle

In [16]:
m = cover_city_compact('SEATTLE', 10)
display(m)

### Washington D.C.

In [17]:
m = cover_city_compact('WASHINGTON D. C.', 7)
display(m)

### Cape Town

In [18]:
m = cover_city_compact('CAPE TOWN', 9)
display(m)

## Exploring Compactness
Compacting essentially lowers the resolution of some grid cells to reduce the overall number of cells it takes to cover a polygon.  The level of compactness depends on the shape and orientation of the polygon.  A square shows a high level of compacting around the middle with increasingly higher resolution cells as we move away from the center.

In [19]:
def cover_compact(geom, res):
    hexagons = h3.polyfill(geom, res, geo_json_conformant=True)
    normal_res = [h3.h3_get_resolution(x) for x in hexagons]
    print("Normal resolution range: {}".format([min(normal_res), max(normal_res)]))
    compacted = h3.compact(hexagons)
    compacted_res = [h3.h3_get_resolution(x) for x in compacted]
    print("Compacted resolution range: {}".format([min(compacted_res), max(compacted_res)]))
    print("Compacting removed {} hexagons".format(len(hexagons)-len(compacted)))
    m = folium.Map(location=geom['coordinates'][0][0][::-1], tiles='stamenterrain')
    poly = folium.GeoJson(geom, name='geojson').add_to(m)
    m = visualize_hexagons(compacted, folium_map=m)
    return m

In [20]:
test_square = {
        "type": "Polygon",
        "coordinates": [
          [
            [
              -71.4385986328125,
              42.12267315117256
            ],
            [
              -70.69427490234375,
              42.12267315117256
            ],
            [
              -70.69427490234375,
              42.627896481020855
            ],
            [
              -71.4385986328125,
              42.627896481020855
            ],
            [
              -71.4385986328125,
              42.12267315117256
            ]
          ]
        ]
      }

m = cover_compact(test_square, 8)
display(m)

Normal resolution range: [8, 8]
Compacted resolution range: [5, 8]
Compacting removed 4104 hexagons


Less conventional shapes aren't compacted as consistently.  Using a resolution that is too course for the input shape can have weird consequences.

In [21]:
test_weird = {
        "type": "Polygon",
        "coordinates": [
          [
            [
              -71.05167388916014,
              42.38847290951024
            ],
            [
              -71.07158660888672,
              42.39455841668649
            ],
            [
              -71.07192993164062,
              42.420415239489934
            ],
            [
              -71.07913970947266,
              42.39886862727977
            ],
            [
              -71.1038589477539,
              42.41357182361187
            ],
            [
              -71.07158660888672,
              42.38517634676783
            ],
            [
              -71.04961395263672,
              42.381879610913195
            ],
            [
              -71.05579376220703,
              42.37249564598936
            ],
            [
              -71.07673645019531,
              42.36463232550283
            ],
            [
              -71.0921859741211,
              42.357782825014176
            ],
            [
              -71.11587524414062,
              42.356514317057886
            ],
            [
              -71.11347198486328,
              42.352708639553654
            ],
            [
              -71.07707977294922,
              42.352708639553654
            ],
            [
              -71.05957031249999,
              42.36666166373274
            ],
            [
              -71.04995727539062,
              42.365900669578544
            ],
            [
              -71.05510711669922,
              42.34788778389048
            ],
            [
              -71.0430908203125,
              42.35220119847454
            ],
            [
              -71.03828430175781,
              42.34027515373573
            ],
            [
              -71.01631164550781,
              42.33900629242653
            ],
            [
              -70.98197937011717,
              42.357782825014176
            ],
            [
              -70.9830093383789,
              42.39810802339276
            ],
            [
              -71.02249145507812,
              42.42016179296033
            ],
            [
              -71.04961395263672,
              42.41053006572743
            ],
            [
              -71.05167388916014,
              42.38847290951024
            ]
          ]
        ]
      }

m = cover_compact(test_weird, 8)
display(m)

Normal resolution range: [8, 8]
Compacted resolution range: [7, 8]
Compacting removed 30 hexagons


Using a higher resolution creates a more accurate representation of the polygon.  In either case, the lowest compacted resolution is 7.  The lowerst compacted resolution is dependent on the shape of the polygon.

In [22]:
m = cover_compact(test_weird, 10)
display(m)

Normal resolution range: [10, 10]
Compacted resolution range: [7, 10]
Compacting removed 2604 hexagons


### Interactive Compacting
Draw a polygon on the map to see its compacted representation.  Use the slider at the bottom of the map to adjust resolution.

In [24]:
res = 8

m = Map(
    layers=(basemap_to_tiles(basemaps.Stamen.Terrain), ),
    center=(0, 0),
    zoom=4,
    scroll_wheel_zoom=True,
)

draw_control = DrawControl()
draw_control.rectangle = {
    "shapeOptions": {
        "fillColor": "#bdbdbd",
        "color": "#bdbdbd",
        "fillOpacity": 0.6
    }
}
def handle_draw(self, action, geo_json):
    if action == 'created':
        print(res.value)
        poly = geo_json['geometry']
        hexagons = h3.polyfill(poly, res.value, geo_json_conformant=True)
        compacted = h3.compact(hexagons)
        multipoly = []
        for poly in compacted:
            polygons = h3.h3_set_to_multi_polygon([poly], geo_json=False)
            outlines = [loop for polygon in polygons for loop in polygon]
            polyline = [outline + [outline[0]] for outline in outlines][0]
            multipoly.append(polyline)
        multipoly_plot = Polygon(locations=multipoly)
        m.add_layer(multipoly_plot)
        
res = widgets.IntSlider(value=8, min=0, max=15, description="Resolution:")
draw_control.on_draw(handle_draw)
m.add_control(draw_control)

items = widgets.VBox([m, res])
display(items)

1


## Hierarchical Spatial Database with H3
Because of its hierarchical nature, H3 allows us to build very simple and fast spatial databases using a tree structure.  The H3 base cells act as the starting nodes of the tree (122 in total).  Each node then inherits 7 child nodes, one for each grid cell number (0-6).  Our tree model can have a maximum of 16 levels, the root level (starting nodes) and one for each possible resolution level (1-15).  Below is a simple python implementation of a Spatial Databse with H3 (adopted from [here](https://blog.zen.ly/geospatial-indexing-on-hilbert-curves-2379b929addc)).

In [25]:
NUM_BASE_CELLS = 122
START_BIT = 15

class Node(object):
    
    def __init__(self, parent):
        self.parent = parent
        self.children = [None, None, None, None, None, None, None]
        self.values = []
        self.resolution = 0
        if self.parent:
            self.resolution = self.parent.resolution+1

class Tree(object):
    
    def __init__(self):
        self.nodes = tuple([Node(None) for _ in range(NUM_BASE_CELLS)])
    
    def add(self, h3_addresses, value):
        for h3_address in h3_addresses:
            resolution = h3.h3_get_resolution(h3_address)
            base_cell = h3.h3_get_base_cell(h3_address)
            # Get base cell node
            curr_node = self.nodes[base_cell]
            # Add each parent starting with resolution 1
            for res in range(1, resolution):
                parent = h3.h3_to_parent(h3_address, res)
                # Figure out the cell number of the parent
                index = h3.string_to_h3(parent)
                bits = bin(index)[2:]
                start = START_BIT + (3 * res) - 3
                cell_number = int(bits[start:start+3], 2)
                if not curr_node.children[cell_number]:
                    curr_node.children[cell_number] = Node(curr_node)

                curr_node = curr_node.children[cell_number]

            # Append value to last node
            if value not in curr_node.values:
                curr_node.values.append(value)
    
    def search(self, h3_address):
        base_cell = h3.h3_get_base_cell(h3_address)
        resolution = h3.h3_get_resolution(h3_address)
        curr_node = self.nodes[base_cell]
        accum_values = []
        for res in range(1, resolution):
            parent = h3.h3_to_parent(h3_address, res)
            index = h3.string_to_h3(parent)
            bits = bin(index)[2:]
            start = START_BIT + (3 * res) - 3
            cell_number = int(bits[start:start+3], 2)
            curr_node = curr_node.children[cell_number]
            if not curr_node:
                return accum_values
            if curr_node.values:
                accum_values = accum_values + curr_node.values
        return accum_values

### World Cities
We will use our implementation to create a spatial database of 36,432 world cities from the geojson file we were workign with earlier.  Each city will be represented by a compacted coverage of H3 cells.  We'll load our data at resolution 8 and then query our database with a list of randomly generated points.

In [26]:
tree = Tree()

# Loading cities
hexcount = 0
with open('cities.geojson', 'r') as geoj:
    cities = json.load(geoj)['features']
    for item in tqdm(cities):
        cityname = item['properties']['NAME']
        geometry = item['geometry']
        hexagons = h3.polyfill(geometry, 8, geo_json_conformant=True)
        compacted = h3.compact(hexagons)
        hexcount+=len(compacted)
        data = json.dumps({'cityname': cityname,
                           'geometry': geometry})
        tree.add(compacted, data)
print("Added {} hexagons to tree".format(hexcount))

100%|██████████| 36432/36432 [00:15<00:00, 2383.96it/s]

Added 301571 hexagons to tree


In [28]:
# Searching 1 million randomly generated points
res = 8
responses = []
for x in tqdm(range(1000000)):
    x, y = uniform(-180,180), uniform(-90,90)
    h3_address = h3.geo_to_h3(y, x, res)
    response = tree.search(h3_address)
    if len(response) > 0:
        responses.append([response, (x,y)])
    

100%|██████████| 1000000/1000000 [00:12<00:00, 82355.34it/s]


In [29]:
for item in responses[:10]:
    data = json.loads(item[0][0])
    print("{} - {}".format(data['cityname'], item[1]))

KOYBAGAR - (65.01537327582218, 52.30286258601231)
NEYA - (43.89723662824986, 58.27093190607101)
NAPLES PARK - (-81.83163879373859, 26.276666199578713)
PROKOPYEVSK - (86.64289979705899, 53.95644800756037)
VICTORIA - (-72.30795178645045, -38.22888274654376)
None - (-80.05399566210271, 41.04400599116124)
MODESTO - (-120.94607410637146, 37.684947469477606)
TRACY - (-121.4309030045233, 37.763035057473715)
COUNTESS WEAR - (-3.477680006130214, 50.69617009298398)
ISLIP - (-73.43424221740915, 40.658642254719695)


## Mapping Query Results
The below cell defines a function which shows the query point and city boundary for a random city returned in the query result.

In [30]:
def visualize_query_response(responses):
    random_result = responses[randrange(len(responses))]
    data = json.loads(random_result[0][0])
    cityname = data['cityname']
    print(cityname)
    geometry = data['geometry']
    query_point = random_result[1]
    m = folium.Map(location=query_point[::-1], tiles='stamenterrain')
    poly = folium.GeoJson(geometry, name='geojson').add_to(m)
    marker = folium.Marker(query_point[::-1], popup="Query Point").add_to(m)
    return m

In [31]:
m = visualize_query_response(responses)
display(m)

MTWALUME


## Bounding Boxes
The above example is a PIP (point-in-polygon) query.  If we want to query the database with a bounding box we need to use the `h3.polyfill` function to generate a list of H3 cells contained by our bounding box.  We then run a PIP query for each H3 cell.  Our implementation doesn't support multiprocessing, but this operation could easily be scaled horizontally.

In [32]:
def bbox_query(geojson, tree, res, compact=False):
    h3_bbox = h3.polyfill(geojson, res, geo_json_conformant=True)
    if compact:
        h3_bbox = h3.compact(h3_bbox)
    ret_cities = []
    for item in h3_bbox:
        response = tree.search(item)
        if len(response) > 0:
            data = json.loads(response[0])
            if data['cityname'] not in ret_cities and data['cityname'] != None:
                ret_cities.append(data['cityname'])
    return ret_cities

Let's use `ipythonleaflet` to build an interactive leaflet map for performing spatial queries on our database.  Use the drawing tools on the left hand side of the map to draw a polygon.  After a few seconds, all cities in our database which intersect the polygon will be printed.

In [33]:
m = Map(
    layers=(basemap_to_tiles(basemaps.Stamen.Terrain), ),
    center=(0, 0),
    zoom=4,
    scroll_wheel_zoom=True,
)

draw_control = DrawControl()
draw_control.rectangle = {
    "shapeOptions": {
        "fillColor": "#fca45d",
        "color": "#fca45d",
        "fillOpacity": 0.6
    }
}
def handle_draw(self, action, geo_json):
    if action == 'created':
        poly = geo_json['geometry']
        resp = bbox_query(poly, tree, 8)
        if len(resp) > 0 and resp[0] != None:
            print(sorted(resp))
        else:
            print("No cities found in database")
        
draw_control.on_draw(handle_draw)
m.add_control(draw_control)

m

Map(basemap={'url': 'https://{s}.tile.openstreetmap.org/{z}/{x}/{y}.png', 'max_zoom': 19, 'attribution': 'Map …

## Optimizing Queries
The output and efficiency of the spatial query varies based on the resolution of the index data, resolution of query, shape/size of the query polygon, and whether or not the polygon is compacted.  Let's define a more robust `bbox_query` method for testing.

In [34]:
def bbox_query(geojson, tree, res, compact=False):
    start = time.time()
    h3_bbox = h3.polyfill(geojson, res, geo_json_conformant=True)
    if compact:
        h3_bbox = h3.compact(h3_bbox)
    gen_cells_time = time.time()
    ret_cities = []
    for item in h3_bbox:
        response = tree.search(item)
        if len(response) > 0:
            data = json.loads(response[0])
            if data['cityname'] not in ret_cities and data['cityname'] != None:
                ret_cities.append(data['cityname'])
    query_db_time = time.time()
    return {'hexcount': len(h3_bbox),
            'cities': ret_cities,
            'num_cities': len(ret_cities),
            'time_gen_cells': gen_cells_time-start,
            'time_query_db': query_db_time-gen_cells_time,
            'resolution': res,
            'compact': compact
           }

Check the performance of the spatial query using all possible input combinations.  Stopping at resolution 10 because anything past that is really slow due to the number of hexagons created with `polyfill`.  Plot the output as a pandas dataframe.

In [35]:
boston_geoj = {
        "type": "Polygon",
        "coordinates": [
          [
            [
              -71.4385986328125,
              42.12267315117256
            ],
            [
              -70.69427490234375,
              42.12267315117256
            ],
            [
              -70.69427490234375,
              42.627896481020855
            ],
            [
              -71.4385986328125,
              42.627896481020855
            ],
            [
              -71.4385986328125,
              42.12267315117256
            ]
          ]
        ]
      }

geojs = [boston_geoj]
resolutions = list(range(0,11))
compact = [True, False]

args = list(itertools.product(geojs, [tree], resolutions, compact))
print("Number of iterations: {}".format(len(args)))

Number of iterations: 22


In [36]:
resp_list = []
for arg in args:
    resp = bbox_query(arg[0], arg[1], arg[2], compact=arg[3])
    resp_list.append(resp)

In [37]:
df = pd.DataFrame(resp_list)
df

cities  compact  hexcount  \
0                                                  []     True         0   
1                                                  []    False         0   
2                                                  []     True         0   
3                                                  []    False         0   
4                                                  []     True         0   
5                                                  []    False         0   
6                                                  []     True         0   
7                                                  []    False         0   
8                                                  []     True         2   
9                                                  []    False         2   
10                                                 []     True        13   
11                                                 []    False        13   
12                                                 []     True        39   
13                                           [BOSTON]    False        93   
14                               [FRAMINGHAM, LOWELL]     True       131   
15          [BOSTON, LYNN, FRAMINGHAM, LOWELL, SALEM]    False       653   
16  [LOWELL, HUMAROCK, ROCKLAND, FRAMINGHAM, HOLLI...     True       420   
17  [LOWELL, BOSTON, SALEM, FRAMINGHAM, MILLIS, LY...    False      4524   
18  [LOWELL, HUMAROCK, BROCKTON, FRAMINGHAM, MAYNA...     True      1055   
19  [WENHAM, LOWELL, BOSTON, BROCKTON, SCITUATE, L...    False     31679   
20  [BROCKTON, LOWELL, LAWRENCE, HOLLISTON, FRAMIN...     True      2977   
21  [FRAMINGHAM, SILVER LAKE, BOSTON, LYNN, COHASS...    False    221605   

    num_cities  resolution  time_gen_cells  time_query_db  
0            0           0        0.000191   4.768372e-07  
1            0           0        0.000129   4.768372e-07  
2            0           1        0.000091   2.384186e-07  
3            0           1        0.000295   7.152557e-07  
4            0           2        0.000198   7.152557e-07  
5            0           2        0.000067   4.768372e-07  
6            0           3        0.000068   9.536743e-07  
7            0           3        0.000057   4.768372e-07  
8            0           4        0.000126   5.197525e-05  
9            0           4        0.000080   4.696846e-05  
10           0           5        0.000190   2.932549e-04  
11           0           5        0.000120   2.436638e-04  
12           0           6        0.000592   7.705688e-04  
13           1           6        0.000397   5.627871e-03  
14           2           7        0.003373   3.833055e-03  
15           5           7        0.002486   8.014536e-02  
16          10           8        0.013548   8.644342e-03  
17          33           8        0.008536   4.536190e-01  
18          12           9        0.129846   3.620553e-02  
19          35           9        0.086789   3.211909e+00  
20          12          10        0.565242   7.215524e-02  
21          35          10        0.444978   2.667086e+01

#### Resolution
Higher resolution queries are more accurate spatially because each hex cell is a smaller size which enables `polyfill` to do a better job when building a representation of the input polygon.  By looking at the higher resolution queries, we can assume that our geojson contains 35 cities.  Only non-compact queries above resolution 9 return the full number of cities.  The query at resolution 8, the same resolution at which our data was indexed, returns 33/35 cities.  A good rule of thumb is to ensure that you are quering your data at a similar or higher resolution than how it is indexed.  The downside of higher resolution queries is that more hexagon cells need to be processed and it takes longer to generate the initial `polyfill`.

#### Compact
At each resolution the compact query returned less cities, maxing out at 12 cities returned at resolution 10.  This is due to the design of our database.  The database only indexes a cities name at the highest resolution node in the tree.  Compacting the query polygon reduces the resolution of some of the hexagon cells to reduce the number of hexagons required to fill the polygon.  If a compacted area is indexed at resolution 7 but is compacted to resolution 6, the query wont work because our starting resolution is too fine.  A potential solution is indexing the city name at all resolutions.

Compacting does save a lot of time when querying the database by reducing the number of hexagons.  At resolution 10, the compacted polygon contains 98.6% less hexagons than its non-compacted version.  The compaction takes an extra 0.12 seconds but saves 2.3 seconds when querying the database.